In [25]:
%%capture
pip install pytorch

In [26]:
%%capture
pip install tqdm

In [ ]:
import torch
import numpy as np
from enum import Enum
import matplotlib.pyplot as plt
import tqdm

In [ ]:
# %load ctrnn/datagen.py
import random
import numpy as np

khz = 1000

def random_size():
    return random.randint(5,10)

def random_times(freq):
    sample_rate = 44.1*khz
    period = 2*np.pi*1.0/freq
    times = np.arange(0, period, 1.0/sample_rate)
    return times

def random_phase():
    return np.pi*random.random()

def random_noise():
    return abs(0.3*random.random())

def random_freq(exclude):
    l,h = exclude
    while True:
        freq = 20.0*khz*random.random()
        if not (freq >= l and freq <= h):
            return freq

def sine(inputs,freq,ampl,phase):
    return ampl*np.sin(freq*np.array(inputs)+phase)

def uniform(inputs,value):
    return np.array([value]*len(inputs))

def random_wakeme():
    freq = 8.0*khz
    times = random_times(10*khz)
    noise = np.random.normal(0,0.3,len(times))
    signal = uniform(times,1)
    data = signal
    cat = Category.WAKEME
    return (data,cat)

def random_ignore():
    times = random_times(10*khz)
    noise = np.random.normal(0,0.3,len(times))
    signal = uniform(times,0.0)
    data = signal
    cat = Category.IGNORE
    return (data,cat)

def random_example():
    idx = random.randint(0,1)
    cat = Category.from_code(idx)
    if cat == Category.WAKEME:
        return random_wakeme()
    else:
        return random_ignore()


In [ ]:
# %load ctrnn/category.py
class Category(Enum):
    WAKEME = "WAKEME"
    IGNORE = "IGNORE"
    UNKNOWN = "UNKNOWN"
    def code(self):
        if self == Category.WAKEME:
            return 0
        else:
            return 1
        
    @staticmethod
    def from_code(code):
        mapping = {0:Category.WAKEME, 1:Category.IGNORE}
        return mapping[code]
    
    @staticmethod
    def series():
        return [Category.WAKEME, Category.IGNORE]



In [ ]:
def gen_dataset(npos=15,nneg=15):
    dataset = []
    dataset += list(map(lambda _: random_wakeme(), range(npos)))
    dataset += list(map(lambda _: random_ignore(), range(nneg)))
    return dataset

def evaluate_genomes(genomes, config, dataset, evaluate, fitness, thresh):
    for genome_id, genome in genomes:
        net = neat.nn.FeedForwardNetwork.create(genome, config)
        
        genome.fitness = 0.0
        for sig,cat in dataset:
            avg_cat = evaluate(net,sig,cat)
            fitval = fitness(avg_cat,cat,thresh)
            if fitval > 0:
                genome.fitness += 1.0/len(dataset)
            
          
        
def test_network(winner,config, evaluate, classify,thresh):
    winner_net = neat.nn.FeedForwardNetwork.create(winner,config)
    fp = 0
    fn = 0
    tp = 0
    tn = 0
    for i in range(1000):
        (sig,cat) = random_example()
        avg_cat = evaluate(winner_net,sig,cat)
        pred_cat = classify(avg_cat,thresh)
        if pred_cat == cat:
            if cat == Category.WAKEME:
                tp += 100.0/1000
            else:
                tn += 100.0/1000
                
        else:
            if cat == Category.WAKEME:
                fn += 100.0/1000
            else:
                fp += 100.0/1000
                
    print("tp=%f tn=%f fp=%f fn=%f" % (tp,tn,fp,fn))
        

In [ ]:
import neat

In [ ]:
CONTENT = '''
[NEAT]
fitness_criterion     = max
fitness_threshold     = 0.7
pop_size              = 250
reset_on_extinction   = 0

[DefaultGenome]
num_inputs              = 1
num_hidden              = 1
num_outputs             = 1
initial_connection      = partial_direct 0.5
feed_forward            = True
compatibility_disjoint_coefficient    = 1.0
compatibility_weight_coefficient      = 0.6
conn_add_prob           = 0.2
conn_delete_prob        = 0.2
node_add_prob           = 0.2
node_delete_prob        = 0.2
activation_default      = sigmoid
activation_options      = sigmoid
activation_mutate_rate  = 0.0
aggregation_default     = sum
aggregation_options     = sum
aggregation_mutate_rate = 0.0
bias_init_mean          = 0.0
bias_init_stdev         = 1.0
bias_replace_rate       = 0.1
bias_mutate_rate        = 0.7
bias_mutate_power       = 0.5
bias_max_value          = 30.0
bias_min_value          = -30.0
response_init_mean      = 1.0
response_init_stdev     = 0.0
response_replace_rate   = 0.0
response_mutate_rate    = 0.0
response_mutate_power   = 0.0
response_max_value      = 30.0
response_min_value      = -30.0

weight_max_value        = 30
weight_min_value        = -30
weight_init_mean        = 0.0
weight_init_stdev       = 1.0
weight_mutate_rate      = 0.8
weight_replace_rate     = 0.1
weight_mutate_power     = 0.5
enabled_default         = True
enabled_mutate_rate     = 0.01

[DefaultSpeciesSet]
compatibility_threshold = 3.0

[DefaultStagnation]
species_fitness_func = max
max_stagnation  = 20

[DefaultReproduction]
elitism            = 2
survival_threshold = 0.2

'''

with open("config.txt", "w") as fh:
    fh.write(CONTENT)
    

In [ ]:
def evaluate(net,sig,cat):
    (sig,cat) = random_example()
    cats = []
    for xi in sig:
        output = net.activate([xi])[0]
        cats.append(output)

    # normalize
    avg_cat = np.mean(cats)
    assert(avg_cat <= 1.0 and avg_cat >= -1.0)
    return avg_cat

def fitness(avg_cat,cat,thresh):
    mag = abs(abs(avg_cat)-thresh)
    
    if cat == Category.WAKEME:
        return mag if avg_cat >= thresh else -mag
    else:
        return -mag if avg_cat >= thresh else mag
    
dataset = gen_dataset(50,50)
def evaluate_tl(net,cfg):
    return evaluate_genomes(net,cfg,dataset,evaluate,fitness,0.5)

# Load configuration.
config = neat.Config(neat.DefaultGenome, neat.DefaultReproduction,
                     neat.DefaultSpeciesSet, neat.DefaultStagnation,
                     'config.txt')

print("create population")
# Create the population, which is the top-level object for a NEAT run.
p = neat.Population(config)

# Add a stdout reporter to show progress in the terminal.
p.add_reporter(neat.StdOutReporter(False))

# Run until a solution is found.
winner = p.run(evaluate_tl)


create population

 ****** Running generation 0 ****** 

Population's average fitness: 0.50000 stdev: 0.00000
Best fitness: 0.50000 - size: (1, 0) - species 1 - id 1
Average adjusted fitness: -0.000
Mean genetic distance 0.628, standard deviation 0.434
Population of 150 members in 1 species
Total extinctions: 0
Generation time: 1.264 sec

 ****** Running generation 1 ****** 

Population's average fitness: 0.49960 stdev: 0.00774
Best fitness: 0.52000 - size: (1, 1) - species 1 - id 215
Average adjusted fitness: 0.090
Mean genetic distance 0.764, standard deviation 0.514
Population of 150 members in 1 species
Total extinctions: 0
Generation time: 1.311 sec (1.287 average)

 ****** Running generation 2 ****** 

Population's average fitness: 0.49987 stdev: 0.01770
Best fitness: 0.60000 - size: (1, 1) - species 1 - id 215
Average adjusted fitness: 0.080
Mean genetic distance 0.870, standard deviation 0.604
Population of 150 members in 1 species
Total extinctions: 0
Generation time: 1.434 se

Population's average fitness: 0.49847 stdev: 0.04024
Best fitness: 0.61000 - size: (3, 4) - species 1 - id 3680
Average adjusted fitness: 0.108
Mean genetic distance 1.604, standard deviation 0.331
Population of 150 members in 1 species
Total extinctions: 0
Generation time: 2.059 sec (2.240 average)

 ****** Running generation 25 ****** 

Population's average fitness: 0.49947 stdev: 0.03577
Best fitness: 0.61000 - size: (4, 4) - species 1 - id 3747
Average adjusted fitness: 0.119
Mean genetic distance 1.647, standard deviation 0.353
Population of 150 members in 1 species
Total extinctions: 0
Generation time: 2.022 sec (2.212 average)

 ****** Running generation 26 ****** 

Population's average fitness: 0.49973 stdev: 0.03973
Best fitness: 0.63000 - size: (4, 4) - species 1 - id 3896
Average adjusted fitness: 0.120
Mean genetic distance 1.683, standard deviation 0.303
Population of 150 members in 1 species
Total extinctions: 0
Generation time: 2.122 sec (2.191 average)

 ****** Running 

Population's average fitness: 0.49973 stdev: 0.03640
Best fitness: 0.64000 - size: (3, 1) - species 1 - id 7127
Average adjusted fitness: 0.119
Mean genetic distance 2.218, standard deviation 0.583
Population of 150 members in 4 species
Total extinctions: 0
Generation time: 2.293 sec (2.288 average)

 ****** Running generation 50 ****** 

Population's average fitness: 0.49827 stdev: 0.04028
Best fitness: 0.63000 - size: (3, 1) - species 1 - id 7127
Average adjusted fitness: 0.136
Mean genetic distance 2.179, standard deviation 0.581
Population of 150 members in 4 species
Total extinctions: 0
Generation time: 2.275 sec (2.285 average)

 ****** Running generation 51 ****** 

Population's average fitness: 0.50467 stdev: 0.03764
Best fitness: 0.61000 - size: (6, 7) - species 3 - id 7332
Average adjusted fitness: 0.094
Mean genetic distance 2.154, standard deviation 0.651
Population of 150 members in 3 species
Total extinctions: 0
Generation time: 2.740 sec (2.324 average)

 ****** Running 

Population's average fitness: 0.49900 stdev: 0.03840
Best fitness: 0.62000 - size: (6, 4) - species 5 - id 10896
Average adjusted fitness: 0.099
Mean genetic distance 2.394, standard deviation 0.591
Population of 150 members in 2 species
Total extinctions: 0
Generation time: 2.703 sec (2.293 average)

 ****** Running generation 75 ****** 

Population's average fitness: 0.50067 stdev: 0.03827
Best fitness: 0.60000 - size: (7, 7) - species 5 - id 10997
Average adjusted fitness: 0.110
Mean genetic distance 2.344, standard deviation 0.589
Population of 150 members in 2 species
Total extinctions: 0
Generation time: 2.277 sec (2.307 average)

 ****** Running generation 76 ****** 

Population's average fitness: 0.50660 stdev: 0.04195
Best fitness: 0.62000 - size: (8, 7) - species 4 - id 11079
Average adjusted fitness: 0.147
Mean genetic distance 2.471, standard deviation 0.675
Population of 150 members in 3 species
Total extinctions: 0
Generation time: 2.150 sec (2.314 average)

 ****** Runni

Population's average fitness: 0.50040 stdev: 0.03673
Best fitness: 0.60000 - size: (7, 9) - species 5 - id 13972
Average adjusted fitness: 0.121
Mean genetic distance 2.471, standard deviation 0.571
Population of 151 members in 6 species
Total extinctions: 0
Generation time: 2.245 sec (2.540 average)

 ****** Running generation 99 ****** 

Population's average fitness: 0.50040 stdev: 0.04051
Best fitness: 0.61000 - size: (3, 1) - species 4 - id 14431
Average adjusted fitness: 0.150
Mean genetic distance 2.439, standard deviation 0.562
Population of 151 members in 6 species
Total extinctions: 0
Generation time: 2.265 sec (2.523 average)

 ****** Running generation 100 ****** 

Population's average fitness: 0.50649 stdev: 0.03441
Best fitness: 0.64000 - size: (7, 5) - species 8 - id 14477
Average adjusted fitness: 0.068
Mean genetic distance 2.514, standard deviation 0.655
Population of 151 members in 5 species
Total extinctions: 0
Generation time: 2.206 sec (2.487 average)

 ****** Runn

...

Population's average fitness: 0.50233 stdev: 0.04592
Best fitness: 0.63000 - size: (15, 12) - species 1003 - id 2113328
Average adjusted fitness: 0.132
Mean genetic distance 2.387, standard deviation 0.644
Population of 150 members in 2 species
Total extinctions: 0
Generation time: 2.366 sec (2.385 average)

 ****** Running generation 14655 ****** 

Population's average fitness: 0.50093 stdev: 0.04196
Best fitness: 0.63000 - size: (22, 11) - species 1002 - id 2113396
Average adjusted fitness: 0.141
Mean genetic distance 2.377, standard deviation 0.732
Population of 150 members in 2 species
Total extinctions: 0
Generation time: 2.362 sec (2.381 average)

 ****** Running generation 14656 ****** 

Population's average fitness: 0.50020 stdev: 0.04186
Best fitness: 0.63000 - size: (24, 26) - species 1002 - id 2113585
Average adjusted fitness: 0.100
Mean genetic distance 2.425, standard deviation 0.721
Population of 150 members in 2 species
Total extinctions: 0
Generation time: 2.917 sec (2.

Population's average fitness: 0.49920 stdev: 0.04501
Best fitness: 0.63000 - size: (17, 13) - species 1004 - id 2116692
Average adjusted fitness: 0.129
Mean genetic distance 2.387, standard deviation 0.730
Population of 150 members in 2 species
Total extinctions: 0
Generation time: 2.287 sec (2.359 average)

 ****** Running generation 14679 ****** 

Population's average fitness: 0.50353 stdev: 0.04475
Best fitness: 0.62000 - size: (24, 22) - species 1002 - id 2116887
Average adjusted fitness: 0.104
Mean genetic distance 2.391, standard deviation 0.699
Population of 150 members in 2 species
Total extinctions: 0
Generation time: 2.725 sec (2.407 average)

 ****** Running generation 14680 ****** 

Population's average fitness: 0.49687 stdev: 0.04162
Best fitness: 0.62000 - size: (23, 17) - species 1002 - id 2117064
Average adjusted fitness: 0.127
Mean genetic distance 2.413, standard deviation 0.684
Population of 150 members in 2 species
Total extinctions: 0
Generation time: 2.466 sec (2.

Population's average fitness: 0.49647 stdev: 0.03926
Best fitness: 0.61000 - size: (14, 9) - species 1005 - id 2120250
Average adjusted fitness: 0.117
Mean genetic distance 2.713, standard deviation 0.779
Population of 150 members in 3 species
Total extinctions: 0
Generation time: 2.207 sec (2.357 average)

 ****** Running generation 14703 ****** 

Population's average fitness: 0.49887 stdev: 0.03850
Best fitness: 0.59000 - size: (14, 9) - species 1005 - id 2120472
Average adjusted fitness: 0.119
Mean genetic distance 2.691, standard deviation 0.788
Population of 150 members in 3 species
Total extinctions: 0
Generation time: 2.553 sec (2.375 average)

 ****** Running generation 14704 ****** 

Population's average fitness: 0.49980 stdev: 0.04455
Best fitness: 0.64000 - size: (23, 20) - species 1002 - id 2120563
Average adjusted fitness: 0.150
Mean genetic distance 2.657, standard deviation 0.790
Population of 150 members in 3 species
Total extinctions: 0
Generation time: 2.447 sec (2.36

Population's average fitness: 0.50053 stdev: 0.03910
Best fitness: 0.60000 - size: (13, 9) - species 1006 - id 2123796
Average adjusted fitness: 0.121
Mean genetic distance 2.390, standard deviation 0.664
Population of 150 members in 2 species
Total extinctions: 0
Generation time: 2.217 sec (2.252 average)

 ****** Running generation 14727 ****** 

Population's average fitness: 0.50853 stdev: 0.04378
Best fitness: 0.64000 - size: (13, 8) - species 1006 - id 2123938
Average adjusted fitness: 0.139
Mean genetic distance 2.337, standard deviation 0.649
Population of 150 members in 2 species
Total extinctions: 0
Generation time: 2.203 sec (2.250 average)

 ****** Running generation 14728 ****** 

Population's average fitness: 0.49540 stdev: 0.03845
Best fitness: 0.63000 - size: (14, 11) - species 1005 - id 2123993
Average adjusted fitness: 0.095
Mean genetic distance 2.298, standard deviation 0.618
Population of 150 members in 2 species
Total extinctions: 0
Generation time: 2.191 sec (2.23

Population's average fitness: 0.50193 stdev: 0.04449
Best fitness: 0.62000 - size: (19, 13) - species 1008 - id 2127150
Average adjusted fitness: 0.122
Mean genetic distance 2.265, standard deviation 0.682
Population of 150 members in 2 species
Total extinctions: 0
Generation time: 2.163 sec (2.245 average)

 ****** Running generation 14751 ****** 

Population's average fitness: 0.50000 stdev: 0.04032
Best fitness: 0.61000 - size: (16, 13) - species 1007 - id 2127298
Average adjusted fitness: 0.100
Mean genetic distance 2.374, standard deviation 0.656
Population of 150 members in 2 species
Total extinctions: 0
Generation time: 2.158 sec (2.238 average)

 ****** Running generation 14752 ****** 

Population's average fitness: 0.50253 stdev: 0.04577
Best fitness: 0.68000 - size: (8, 1) - species 1007 - id 2127523
Average adjusted fitness: 0.132
Mean genetic distance 2.455, standard deviation 0.629
Population of 150 members in 2 species
Total extinctions: 0
Generation time: 2.190 sec (2.23

In [ ]:

def classify(value,thresh):
    if value >= thresh:
        return Category.WAKEME
    elif value < thresh:
        return Category.IGNORE
    
test_network(winner,config,evaluate,classify,0.5)